<a href="https://colab.research.google.com/github/pujasc/CNNDailyMail/blob/master/Summarization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Data 
The tookenized and chunked Data is fetched from Github Repository.

In [0]:
!git clone https://github.com/pujasc/CNNDailyMail.git
#!ls CNNDailyMail

Cloning into 'CNNDailyMail'...
remote: Enumerating objects: 6, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 335 (delta 1), reused 0 (delta 0), pack-reused 329
Receiving objects: 100% (335/335), 480.37 MiB | 13.78 MiB/s, done.
Resolving deltas: 100% (6/6), done.
Checking out files: 100% (316/316), done.


Creating Word Embeedings from the Chunked binary files.

In [0]:
import glob
import struct
data_path='/content/CNNDailyMail/val_001.bin'
while True:
    filelist = glob.glob(data_path) # get the list of datafiles
    assert filelist, ('Error: Empty filelist at %s' % data_path) # check filelist isn't empty
    for f in filelist:
      reader = open(f, 'rb')
      while True:
        len_bytes = reader.read(8)
        if not len_bytes: break # finished reading this file
        str_len = struct.unpack('q', len_bytes)[0]
        example_str = struct.unpack('%ds' % str_len, reader.read(str_len))[0]
        print(example_str)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



b"\n\x82#\n\xfa\x02\n\x08abstract\x12\xed\x02\n\xea\x02\n\xe7\x02<s> ireland beat zimbabwe by five runs after exciting tie came down to final over but the game was also surrounded by a controversial wicket . </s> <s> john mooney appeared to touch the foam as he caught sean williams out . </s> <s> ed joyce scored his third one-day international century . </s> <s> click here for all the latest cricket world cup news . </s>\n\x82 \n\x07article\x12\xf6\x1f\n\xf3\x1f\n\xf0\x1fireland clung on to claim a controversial five-run win over zimbabwe to keep their bid to reach the world cup quarter-finals on track . ed joyce 's third one-day international century helped ireland post 331 for eight - their highest ever score at a world cup - but zimbabwe looked like running down the record chase until a debatable john mooney catch . replays appeared to show mooney had stepped on the rope when he held on to remove sean williams , who was four short of a century and seemingly in control of the pursuit

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



b"\n\xe0!\n\xac\x01\n\x08abstract\x12\x9f\x01\n\x9c\x01\n\x99\x01<s> family says farkhunda , 27 , made accusations against a local mullah . </s> <s> mullah reportedly began shouting that she had burned the quran . </s>\n\xae \n\x07article\x12\xa2 \n\x9f \n\x9c kabul , afghanistan -lrb- cnn -rrb- grieving women carried her coffin high on their shoulders in scenes many said they had never witnessed before in the afghan capital . men are traditionally pallbearers in kabul , where days earlier a mob of male attackers beat and kicked 27-year-old farkhunda before tossing her off a bridge , setting her body on fire and throwing it in the river . like many afghans , farkhunda used only one name . early reports suggested that farkhunda was mentally ill , but her tearful father , nadir , told cnn affiliate tolonews she was a religious teacher who taught the quran to children . he said there was no way his daughter would burn pages of the holy book , which has been cited as the motive for the hor

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



b"\n\xd2\x0f\n\x8f\x02\n\x08abstract\x12\x82\x02\n\xff\x01\n\xfc\x01<s> york is considered to be the safest city in the world , according to a survey . </s> <s> bath , edinburgh and brighton also make the top four safest places . </s> <s> cairo , bangkok , istanbul and marrakech deemed most risky cities to visit . </s>\n\xbd\r\n\x07article\x12\xb1\r\n\xae\r\n\xab\rit boasts a beautiful town centre and a wealth of history to explore . but it turns out there 's another reason why tourists flock to york -- it 's considered the world 's safest city . and three more british towns -- bath , edinburgh and brighton -- help make up the top four safest places . york is considered the world 's safest city , according to a new study which found only one per cent of people consider it to be risky . cairo , bangkok , istanbul and marrakech were the cities deemed most risky to visit on a short break . the survey by post office travel insurance of 2,075 uk adults showed that 72 per cent felt york was 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [0]:
import glob
import random
import struct
import csv
from tensorflow.core.example import example_pb2

SENTENCE_START = '<s>'
SENTENCE_END = '</s>'
PAD_TOKEN = '[PAD]' 
UNKNOWN_TOKEN = '[UNK]' 
START_DECODING = '[START]' 
STOP_DECODING='[STOP]'
# to represent tthe words for our model
class Vocab(object):
  def __init__(self,vocab_file,vocab_size):
    self._word_to_id = {} #first we map the words to id
    self._id_to_word = {} #creating a reverse dict mapping 
    self._count = 0 #counter for total number of words in vocab, our vocab size is 200000, we need not use all words.

    for w in [UNKNOWN_TOKEN, PAD_TOKEN, START_DECODING, STOP_DECODING]:
      self._word_to_id[w] = self._count
      self._id_to_word[self._count] = w
      self._count += 1
    
    with open(vocab_file, 'r') as vocab_f:
      for line in vocab_f:
        pieces = line.split()
        if len(pieces) != 2:
          print ('Warning: incorrectly formatted line in vocabulary file: %s\n' % line)
          continue
        w = pieces[0]
        if w in [SENTENCE_START, SENTENCE_END, UNKNOWN_TOKEN, PAD_TOKEN, START_DECODING, STOP_DECODING]:
          raise Exception('<s>, </s>, [UNK], [PAD], [START] and [STOP] shouldn\'t be in the vocab file, but %s is' % w)
        if w in self._word_to_id:
          raise Exception('Duplicated word in vocabulary file: %s' % w)
        self._word_to_id[w] = self._count
        self._id_to_word[self._count] = w
        self._count += 1
        if vocab_size != 0 and self._count >= vocab_size:
          print ("max_size of vocab was specified as %i; we now have %i words. Stopping reading." % (vocab_size, self._count))
          #print(self._word_to_id['command'])
          break

    print ("Finished constructing vocabulary of %i total words. Last word added: %s" % (self._count, self._id_to_word[self._count-1]))
  



#Batcher
This is to create batches of the chunked data which will help be essential for multithreading,

In [0]:
import queue as Queue
from random import shuffle
from threading import Thread
import time
import numpy as np
import tensorflow as tf

class Batcher(object):
  BATCH_QUEUE_MAX=100
  def __init__(self,data_path,vocab,hps,single_pass):
    self._data_path = data_path
    self._vocab = vocab
    self._hps = hps
    self._single_pass = single_pass

    # Initialize a queue of Batches waiting to be used, and a queue of Examples waiting to be batched
    self._batch_queue = Queue.Queue(self.BATCH_QUEUE_MAX)
    self._example_queue = Queue.Queue(self.BATCH_QUEUE_MAX * self._hps.batch_size)

    # Different settings depending on whether we're in single_pass mode or not
    if single_pass:
      self._num_example_q_threads = 1 
      self._num_batch_q_threads = 1 
      self._bucketing_cache_size = 1 
      self._finished_reading = False 
    else:
      self._num_example_q_threads = 16 
      self._num_batch_q_threads = 4  
      self._bucketing_cache_size = 100 
    self._example_q_threads = []
    for _ in xrange(self._num_example_q_threads):
      self._example_q_threads.append(Thread(target=self.fill_example_queue))
      self._example_q_threads[-1].daemon = True
      self._example_q_threads[-1].start()
    self._batch_q_threads = []
    for _ in xrange(self._num_batch_q_threads):
      self._batch_q_threads.append(Thread(target=self.fill_batch_queue))
      self._batch_q_threads[-1].daemon = True
      self._batch_q_threads[-1].start()

    # Start a thread that watches the other threads and restarts them if they're dead
    if not single_pass: # We don't want a watcher in single_pass mode because the threads shouldn't run forever
      self._watch_thread = Thread(target=self.watch_threads)
      self._watch_thread.daemon = True
      self._watch_thread.start()

  def next_batch(self):

  def fill_example_queue(self):

  def fill_batch_queue(self):

  def watch_threads(self):

  def text_generator(self,example_generator):


#Run

In [0]:
!ls

CNNDailyMail  sample_data


In [0]:
import tensorflow as tf
import os
import sys
import time
import numpy as np
from collections import namedtuple


def main():
  #if len(unused_argv) != 1: # prints a message if you've entered flags incorrectly
  #  raise Exception("Problem with flags: %s" % unused_argv)
  tf.compat.v1.reset_default_graph()


  tf.compat.v1.logging.set_verbosity(tf.compat.v1.logging.INFO) # choose what level of logging you want
  print(tf.compat.v1.logging.info('Starting seq2seq_attention in %s mode...', (FLAGS.mode)))

  FLAGS.log_root = os.path.join(FLAGS.log_root, FLAGS.exp_name)
  if not os.path.exists(FLAGS.log_root):
    if FLAGS.mode=="train":
      os.makedirs(FLAGS.log_root)
    else:
      raise Exception("Logdir %s doesn't exist. Run in train mode to create it." % (FLAGS.log_root))

  vocab = Vocab(FLAGS.vocab_path, FLAGS.vocab_size) #
  
  if FLAGS.mode == 'decode':
    FLAGS.batch_size = FLAGS.beam_size

  # If single_pass=True, check we're in decode mode
  if FLAGS.single_pass and FLAGS.mode!='decode':
    raise Exception("The single_pass flag should only be True in decode mode")

  # Make a namedtuple hps, containing the values of the hyperparameters that the model needs
  hparam_list = ['mode', 'lr', 'adagrad_init_acc', 'rand_unif_init_mag', 'trunc_norm_init_std', 'max_grad_norm', 'hidden_dim', 'emb_dim', 'batch_size', 'max_dec_steps', 'max_enc_steps', 'coverage', 'cov_loss_wt', 'pointer_gen']
  hps_dict = {}

  flag_members = [attr for attr in dir(FLAGS) if not callable(getattr(FLAGS, attr)) and not attr.startswith("__")]
  for m in flag_members:
    hps_dict[m] = getattr(FLAGS, m)
  
  hps = namedtuple("HParams", hps_dict.keys())(**hps_dict)
  
    # Create a batcher object that will create minibatches of data
  batcher = Batcher(FLAGS.data_path, vocab, hps, single_pass=FLAGS.single_pass)

  tf.set_random_seed(111) # a seed value for randomness

  if hps.mode == 'train':
    print( "creating model...")
    model = SummarizationModel(hps, vocab)
    setup_training(model, batcher)
  elif hps.mode == 'eval':
    model = SummarizationModel(hps, vocab)
    run_eval(model, batcher, vocab)
  elif hps.mode == 'decode':
    decode_model_hps = hps  # This will be the hyperparameters for the decoder model
    decode_model_hps = hps._replace(max_dec_steps=1) # The model is configured with max_dec_steps=1 because we only ever run one step of the decoder at a time (to do beam search). Note that the batcher is initialized with max_dec_steps equal to e.g. 100 because the batches need to contain the full summaries
    model = SummarizationModel(decode_model_hps, vocab)
    decoder = BeamSearchDecoder(model, batcher, vocab)
    decoder.decode() # decode indefinitely (unless single_pass=True, in which case deocde the dataset exactly once)
  else:
    raise ValueError("The 'mode' flag must be one of train/eval/decode")



In [0]:
class flags_:
  pass
FLAGS = flags_()

default_path = "/content/CNNDailyMail/"

# Where to find data
FLAGS.data_path= default_path + 'train_*'	
#FLAGS.data_path= default_path +  'val_*'	
FLAGS.vocab_path= default_path + 'vocab'	

# Important settings
FLAGS.mode= 'train' #'decode'# must be one of train/eval/decode'
FLAGS.single_pass= False 

# Where to save output
FLAGS.log_root= default_path +'logs'#Root directory for all logging.
FLAGS.exp_name= 'myexperiment'#Name for experiment. Logs will be saved in a directory with this name, under log_root.
# Hyperparameters
FLAGS.hidden_dim= 256#, 'dimension of RNN hidden states')
FLAGS.emb_dim= 128#, 'dimension of word embeddings')
FLAGS.batch_size= 16#, 'minibatch size')
FLAGS.max_enc_steps= 400#, 'max timesteps of encoder (max source text tokens)')
FLAGS.max_dec_steps= 100#, 'max timesteps of decoder (max summary tokens)')
FLAGS.beam_size= 16 #4#, 'beam size for beam search decoding.')
FLAGS.min_dec_steps= 35#, 'Minimum sequence length of generated summary. Applies only for beam search decoding mode')
FLAGS.vocab_size= 50000#, 'Size of vocabulary. These will be read from the vocabulary file in order. If the vocabulary file contains fewer words than this number, or if this number is set to 0, will take all words in the vocabulary file.')
FLAGS.lr= 0.15#, 'learning rate')
FLAGS.adagrad_init_acc= 0.1#, 'initial accumulator value for Adagrad')
FLAGS.rand_unif_init_mag= 0.02#, 'magnitude for lstm cells random uniform inititalization')
FLAGS.trunc_norm_init_std= 1e-4#, 'std of trunc norm init, used for initializing everything else')
FLAGS.max_grad_norm= 2.0#, 'for gradient clipping')

# Pointer-generator or baseline model
FLAGS.pointer_gen= True#, 'If True, use pointer-generator model. If False, use baseline model.')

# Coverage hyperparameters
FLAGS.coverage= False#, 'Use coverage mechanism. Note, the experiments reported in the ACL paper train WITHOUT coverage until converged, and then train for a short phase WITH coverage afterwards. i.e. to reproduce the results in the ACL paper, turn this off for most of training then turn on for a short phase at the end.')
FLAGS.cov_loss_wt= 1.0#, 'Weight of coverage loss (lambda in the paper). If zero, then no incentive to minimize coverage loss.')

# Utility flags, for restoring and changing checkpoints
FLAGS.convert_to_coverage_model= False#, 'Convert a non-coverage model to a coverage model. Turn this on and run in train mode. Your current training model will be copied to a new version (same name with _cov_init appended) that will be ready to run with coverage flag turned on, for the coverage training stage.')
FLAGS.restore_best_model= False#, 'Restore the best model in the eval/ dir and save it in the train/ dir, ready to be used for further training. Useful for early stopping, or if your training checkpoint has become corrupted with e.g. NaN values.')

FLAGS.debug= False#, "Run in tensorflow's debug mode (watches for NaN/inf values)"

main()

INFO:tensorflow:Starting seq2seq_attention in train mode...
None








max_size of vocab was specified as 50000; we now have 50000 words. Stopping reading.
3292
Finished constructing vocabulary of 50000 total words. Last word added: perisic


NameError: ignored

In [0]:
print(FLAGS.vocab_path)

vocab
